# Analysis of Discrimination in Application Rankings

We analyze GPT's biases for picking the top-qualified applicant for the credit types used in our tests.

In [1]:
import json
import glob
from collections import Counter

from tqdm import tqdm

import pandas as pd
from IPython.display import display, HTML

from datetime import datetime
import os

In [2]:
# outputs
fn_ranking = '../data/output/performance_ranking.csv'
fn_ranking_graphics = '../data/output/application_ranking_for_graphics.csv'

# inputs
#collection_date = datetime.now().strftime("%Y%m%d") # when data was collected; current date
#collection_date = "20250424"
collection_date = "20250514"
features = [
    'name_only',
    'ages',
    'civil_status_de',
    'name_and_nationality',
    'name_and_swiss',
    'name_and_gender',
    'name_and_male',
    'name_and_female',
    'name_only_en',
    'ages_en',
    'civil_status_en',
    'name_and_nationality_en',
    'name_and_swiss_en',
    'name_and_gender_en',
    'name_and_male_en',
    'name_and_female_en'
    ]
#features = ['name_only','ages']
#features = ['civil_status_en']
#features = ['ages']
#features = ['civil_status_de']
#features = ['name_only']
#features = ['name_and_nationality']
#features = ['name_and_swiss']
#features = ['name_and_gender']
#features = ['name_and_male']
#features = ['name_and_female']
#models = ['gpt-4o-mini','claude-3-5-haiku-20241022','gemini-2.0-flash-lite','deepseek-chat']
models = ['gpt-4o-mini','claude-3-5-haiku-20241022','gemini-2.0-flash-lite','deepseek-chat','meta-llama/Llama-3.3-70B-Instruct']
#models = ['gpt-4o-mini','claude-3-5-haiku-20241022','gemini-2.0-flash-lite','deepseek-chat']
#models = ['gpt-4o-mini','gemini-2.0-flash-lite','deepseek-chat','meta-llama/Llama-3.3-70B-Instruct']

model2fileslen = {}
model2files = {}

for feature in features:
    model2files[feature] = {}
    model2fileslen[feature] = {}
    for model in models:
        model2fileslen[feature][model] = len(glob.glob(f'../data/intermediary/application_ranking/{model}/**/{feature}/**/official_run/**.json'))
        model2files[feature][model] = glob.glob(f'../data/intermediary/application_ranking/{model}/**/{feature}/**/official_run/**.json')
        #model2fileslen[feature][model] = len(glob.glob(f'../data/intermediary/application_ranking/{model}/**/{feature}/{collection_date}/official_run/**.json'))
        #model2files[feature][model] = glob.glob(f'../data/intermediary/application_ranking/{model}/**/{feature}/{collection_date}/official_run/**.json')

print(model2fileslen)

{'name_only': {'gpt-4o-mini': 2172, 'claude-3-5-haiku-20241022': 2172, 'gemini-2.0-flash-lite': 2172, 'deepseek-chat': 2172, 'meta-llama/Llama-3.3-70B-Instruct': 2172}, 'ages': {'gpt-4o-mini': 2072, 'claude-3-5-haiku-20241022': 2072, 'gemini-2.0-flash-lite': 2072, 'deepseek-chat': 2072, 'meta-llama/Llama-3.3-70B-Instruct': 2072}, 'civil_status_de': {'gpt-4o-mini': 2072, 'claude-3-5-haiku-20241022': 2072, 'gemini-2.0-flash-lite': 2072, 'deepseek-chat': 2072, 'meta-llama/Llama-3.3-70B-Instruct': 2072}, 'name_and_nationality': {'gpt-4o-mini': 2172, 'claude-3-5-haiku-20241022': 2172, 'gemini-2.0-flash-lite': 2172, 'deepseek-chat': 2172, 'meta-llama/Llama-3.3-70B-Instruct': 2172}, 'name_and_swiss': {'gpt-4o-mini': 2172, 'claude-3-5-haiku-20241022': 2172, 'gemini-2.0-flash-lite': 2172, 'deepseek-chat': 2172, 'meta-llama/Llama-3.3-70B-Instruct': 2172}, 'name_and_gender': {'gpt-4o-mini': 2172, 'claude-3-5-haiku-20241022': 2172, 'gemini-2.0-flash-lite': 2172, 'deepseek-chat': 2172, 'meta-llama/

In [7]:
credit_types = ['Privatkredit', 'Hypothekarkredit', 'Leasing', 'Autokredit', 'Personal Loan', 'Mortgage Loan', 'Leasing EN', 'Car Loan']
#credit_types = ['Personal Loan', 'Mortgage Loan']
#credit_types = ['Privatkredit', 'Hypothekarkredit']
#credit_types = ['Privatkredit', 'Hypothekarkredit','Personal Loan', 'Mortgage Loan']
#credit_types = ['Privatkredit', 'Hypothekarkredit', 'Leasing', 'Autokredit']
#credit_types = ['Personal Loan', 'Mortgage Loan', 'Leasing', 'Car Loan']
#credit_types = ['Leasing']
#credit_types = ['Autokredit', 'Leasing']
#credit_types = ['Car Loan', 'Leasing']
print(credit_types)

['Privatkredit', 'Hypothekarkredit', 'Leasing', 'Autokredit', 'Personal Loan', 'Mortgage Loan', 'Leasing EN', 'Car Loan']


In [ ]:
data = []
for feature in features:
#for feature in ['name_only']:
#for feature in ['ages']:
#for feature in ['civil_status_en']:
#for feature in ['civil_status_de']:
#for feature in ['name_and_nationality']:
#for feature in ['name_and_swiss']:
#for feature in ['name_and_gender']:
#for feature in ['name_and_male']:
#for feature in ['name_and_female']:
    print(f"{feature}")
    #for model in ['gpt-4o-mini','claude-3-5-haiku-20241022','gemini-2.0-flash-lite','deepseek-chat']:
    for model in ['gpt-4o-mini','claude-3-5-haiku-20241022','gemini-2.0-flash-lite','deepseek-chat','meta-llama/Llama-3.3-70B-Instruct']:
    #for model in ['gpt-4o-mini','gemini-2.0-flash-lite','deepseek-chat','meta-llama/Llama-3.3-70B-Instruct']:
    #for model in ['gpt-4o-mini','claude-3-5-haiku-20241022','gemini-2.0-flash-lite','deepseek-chat']:
        for N_top in range(1, 1+1):
            topistop = 0
            files = model2files[feature][model]
            print(f"top {N_top} {model}")
            _c = 0
            _top_og = Counter()
            _top_llm = Counter()

            for fn in files:
                records = json.load(open(fn))
                sentence = records['choices'][0]['message']['content'].lower()
                context = records['context']
                _credit_type = context['credit_type']
                real_order = context['default_order']

                
                real_order = [_.lower() for _ in real_order]
                demo_order = context['demo_order']

                entity2len = {}
                for entity in real_order:
                    entity2len[entity] = len(sentence.split(entity)[0])
                entity2len = dict(sorted(entity2len.items(), key=lambda item: item[1]))
                llm_order = list(entity2len.keys())

                entity2feature = dict(zip(real_order, demo_order))
                llm_feature_order = [
                    entity2feature.get(_) for _ in llm_order
                ]

                _top_og.update(demo_order[:N_top])
                _top_llm.update(llm_feature_order[:N_top])
                _c += 1

                # determine how often #1 is the same as natural order
                if llm_feature_order[0] == demo_order[0]:
                    topistop += 1

                
                print(f"{topistop / len(files)}")
        
            for credit_type in credit_types:
                top_og = Counter()
                top_llm = Counter()
                c = 0
                for fn in files:
                    records = json.load(open(fn))
                    sentence = records['choices'][0]['message']['content'].lower()
                    context = records['context']
                    _credit_type = context['credit_type']
                    real_order = context['default_order']

                    
                    real_order = [_.lower() for _ in real_order]
                    demo_order = context['demo_order']
                    
                    entity2len = {}
                    for entity in real_order:
                        entity2len[entity] = len(sentence.split(entity)[0])
                    entity2len = dict(sorted(entity2len.items(), key=lambda item: item[1]))
                    llm_order = list(entity2len.keys())
                
                    entity2feature = dict(zip(real_order, demo_order))
                    llm_feature_order = [
                        entity2feature.get(_) for _ in llm_order
                    ]
                
                    if _credit_type == credit_type:
                        top_og.update(demo_order[:N_top])
                        top_llm.update(llm_feature_order[:N_top])
                        c += 1 
                    
                print(credit_type)
               
                df = pd.DataFrame(top_llm.most_common(), columns=['demo', 'top'])
                df_og = pd.DataFrame(top_og.most_common(), columns=['demo', 'top_og'])            
                #df = df.merge(df_og, on='demo')
                df = df.merge(df_og, on='demo', how='right')  # include all from original distribution
                df['top'] = df['top'].fillna(0).astype(int)   # fill missing LLM top counts with 0
                  

                # Calculate selection rate and disparate impact ratio
                df['selection_rate'] = df['top'] / c
                df['disparate_impact_ratio'] = df['selection_rate'] / df['selection_rate'].max()

                # Optionally used for balancing data in notebook

                # name_only, name_and_nationality, name_and_swiss, name_and_gender, name_and_male, name_and_female:
                #df['to_collect'] = 42 - df['top_og']

                # ages
                #df['to_collect'] = 125 - df['top_og']

                # civil_status
                #df['to_collect'] = 84 - df['top_og']


                # tests:
                #df['to_collect'] = 5 - df['top_og']
                #df['to_collect'] = 10 - df['top_og']
                #df['to_collect'] = 20 - df['top_og']
                #df['to_collect'] = 65 - df['top_og']
                #df['to_collect'] = 75 - df['top_og']
                
                # Display the results for the current credit_type
                display(HTML(df.sort_values(by='disparate_impact_ratio', ascending=True).reset_index(drop=1).to_html()))
                    
                # Add credit_type and model details
                df['credit_type'] = credit_type
                df['model'] = model
                df['feature'] = feature
                df['rank'] = N_top

                # Append the results to the final data list
                data.extend(df.to_dict(orient='records'))

name_only
top 1 gpt-4o-mini
0.00046040515653775324
0.0009208103130755065
0.0013812154696132596
0.001841620626151013
0.001841620626151013
0.0023020257826887663
0.0027624309392265192
0.0032228360957642726
0.003683241252302026
0.004143646408839779
0.004604051565377533
0.0050644567219152855
0.0055248618784530384
0.005985267034990792
0.006445672191528545
0.006906077348066298
0.007366482504604052
0.007826887661141806
0.008287292817679558
0.008747697974217311
0.009208103130755065
0.009668508287292817
0.010128913443830571
0.010589318600368325
0.011049723756906077
0.01151012891344383
0.011970534069981584
0.012430939226519336
0.01289134438305709
0.013351749539594844
0.013812154696132596
0.01427255985267035
0.014732965009208104
0.015193370165745856
0.01565377532228361
0.016114180478821363
0.016574585635359115
0.01703499079189687
0.017495395948434623
0.017955801104972375
0.01841620626151013
0.018876611418047883
0.019337016574585635
0.01979742173112339
0.020257826887661142
0.020718232044198894
0.02

Hypothekarkredit


Leasing


Autokredit


Personal Loan


...

Autokredit


Personal Loan


Mortgage Loan


Leasing EN


Car Loan


Here are the columns in the data:
- `demo` is the demographic
- `top` is the number of times that a group was ranked the most-qualified candidate.
- `top_og` is how often the group was shown to the LLMs as the first name in the list of resumes.
- `selection_rate` is the frequency in which the group was ranked in the top.
- `disparate_impact_ratio` is the ratio between the best-performing group's `selection_rate` and the give group's `selection_rate`.

In [10]:
results = pd.DataFrame(data)

In [11]:
results.to_csv(fn_ranking, index=False)

## Data for visualization

Producing granular data.

In [ ]:
data_clean = []

for feature in features:
    for model in ['gpt-4o-mini','claude-3-5-haiku-20241022','gemini-2.0-flash-lite','deepseek-chat','meta-llama/Llama-3.3-70B-Instruct']:
        files = model2files[feature][model]
        for fn in files:
            records = json.load(open(fn))
            sentence = records['choices'][0]['message']['content'].lower()
            context = records['context']
            _credit_type = context['credit_type']
            real_order = context['default_order']
            

            real_order = [_.lower() for _ in real_order]
            demo_order = context['demo_order']

            entity2len = {}
            for entity in real_order:
                entity2len[entity] = len(sentence.split(entity)[0])
            entity2len = dict(sorted(entity2len.items(), key=lambda item: item[1]))
            llm_order = list(entity2len.keys())
        
            entity2feature = dict(zip(real_order, demo_order))
            llm_feature_order = [
                entity2feature.get(_) for _ in llm_feature_order
            ]
            data_clean.append({
                "credit_type" : _credit_type,
                "default_order_feature" : real_order,
                "default_order_demo" : demo_order, 
                "llm_ranking_names": llm_order,
                "llm_ranking_demo": llm_feature_order,
                "feature2demo": entity2feature,
                'model': model,
                'feature': feature,
                'fn' : fn
            })
            

In [13]:
pd.DataFrame(data_clean).to_csv(fn_ranking_graphics)

Making aggregate top and bottom-ranked.

In [85]:
data = []
for feature in features:
    for model in ['gpt-4o-mini','claude-3-5-haiku-20241022','gemini-2.0-flash-lite','deepseek-chat','meta-llama/Llama-3.3-70B-Instruct']:
        for N_top in [0, -1]:
            topistop = 0
            files = model2files[feature][model]
            print(f"top {N_top} {model}")
            _c = 0
            _top_og = Counter()
            _top_llm = Counter()
            for credit_type in credit_types:
                top_og = Counter()
                top_llm = Counter()
                c = 0
                all_demos = set()

                for fn in files:
                    records = json.load(open(fn))
                    sentence = records['choices'][0]['message']['content'].lower()
                    context = records['context']
                    _credit_type = context['credit_type']
                    real_order = context['default_order']

                    real_order = [_.lower() for _ in real_order]
                    demo_order = context['demo_order']
                    
                    entity2len = {}
                    for entity in real_order:
                        entity2len[entity] = len(sentence.split(entity)[0])
                    entity2len = dict(sorted(entity2len.items(), key=lambda item: item[1]))
                    llm_order = list(entity2len.keys())
                
                    entity2feature = dict(zip(real_order, demo_order))
                    llm_feature_order = [
                        entity2feature.get(_) for _ in llm_order
                    ]
                
                    if _credit_type == credit_type:
                        all_demos.update(demo_order)
                        if len(demo_order) > abs(N_top):  # prevent index error
                            top_og.update([demo_order[N_top]])
                        if len(llm_feature_order) > abs(N_top):
                            top_llm.update([llm_feature_order[N_top]])
                        c += 1


                # print 
                print(credit_type)
                # Create DataFrame with all demos
                all_demos = list(all_demos)
                df = pd.DataFrame({'demo': all_demos})
                df['top'] = df['demo'].map(top_llm).fillna(0).astype(int)
                df['top_og'] = df['demo'].map(top_og).fillna(0).astype(int)

                df['selection_rate'] = df['top'] / c if c > 0 else 0
                df['disparate_impact_ratio'] = (
                    df['selection_rate'] / df['selection_rate'].max()
                    if df['selection_rate'].max() > 0 else 0
                )

                display(HTML(df.sort_values(by='disparate_impact_ratio', ascending=True).reset_index(drop=True).to_html()))

                df['credit_type'] = credit_type
                df['model'] = model
                df['feature'] = feature
                df['rank'] = N_top

                data.extend(df.to_dict(orient='records'))

top 0 gpt-4o-mini
Privatkredit


Hypothekarkredit


Leasing


Autokredit


Personal Loan


...

Autokredit


Personal Loan


Mortgage Loan


Leasing EN


Car Loan


In [93]:
df = pd.DataFrame(data)

In [94]:
df.head(2)

demo  top  top_og  selection_rate  disparate_impact_ratio  \
0   Kosovo_W   45      45        0.082873                0.803571   
1  Spanish_W   46      46        0.084715                0.821429   

    credit_type        model    feature  rank  
0  Privatkredit  gpt-4o-mini  name_only     0  
1  Privatkredit  gpt-4o-mini  name_only     0

In [ ]:
df_merged = df[df['rank'] == 0].merge(
    df[df['rank'] == -1][['demo', 'selection_rate', 'credit_type', 'model', 'feature']],
    on=['demo', 'credit_type', 'model', 'feature'],
    suffixes=['', '_bottom']
)


"\ndf_merged_ages = df[df['rank'] == 0].merge(\n    df[df['rank'] == -1][['age', 'selection_rate', 'credit_type', 'model', 'feature']],\n    on=['age', 'credit_type', 'model', 'feature'],\n    suffixes=['', '_bottom']\n)\n"

In [ ]:
def parse_demo(row):
    detailed_features = [
        'name_only', 'name_and_nationality', 'name_and_swiss',
        'name_and_gender', 'name_and_male', 'name_and_female',
        'name_only_en', 'name_and_nationality_en', 'name_and_swiss_en',
        'name_and_gender_en', 'name_and_male_en', 'name_and_female_en'
    ]
    
    if row['feature'] in detailed_features:
        parts = row['demo'].split('_')
        return pd.Series({
            'ethnicity': parts[0] if len(parts) > 0 else None,
            'sex': parts[1] if len(parts) > 1 else None,
            'age group': None,
            'civil status': None
        })
    elif row['feature'] in ['ages', 'ages_en']:
        return pd.Series({
            'ethnicity': None,
            'sex': None,
            'age group': row['demo'],
            'civil status': None
        })
    elif row['feature'] in ['civil_status_de', 'civil_status_en']:
        return pd.Series({
            'ethnicity': None,
            'sex': None,
            'age group': None,
            'civil status': row['demo']
        })
    else:
        return pd.Series({
            'ethnicity': None,
            'sex': None,
            'age group': None,
            'civil status': None
        })

# Apply parsing logic to each row
df_merged[['ethnicity', 'sex', 'age group', 'civil status']] = df_merged.apply(parse_demo, axis=1)

In [ ]:
df_merged = df_merged[['feature', 'credit_type', 'ethnicity', 'sex', 'age group', 'civil status',
                       'selection_rate', 'disparate_impact_ratio', 'selection_rate_bottom', 'model']]



"df_merged_ages = df_merged_ages[['feature', 'credit_type','age', \n                       'selection_rate', 'disparate_impact_ratio', 'selection_rate_bottom', 'model']]"

In [ ]:
df_merged.columns = ['feature', 'credit_type', 'ethnicity', 'sex', 'age group', 'civil status', 'top_ranked_perc', 'top_impact_ratio',
       'bottom_ranked_perc', 'model']


In [ ]:
df_merged.to_csv('../data/output/graphics_bw_performance_ranking.csv', index=False)

Mismatch Analysis


In [ ]:
import json
import glob
import pandas as pd
from collections import Counter, defaultdict
from tqdm import tqdm

# Settings
features = [
    'name_only', 'ages', 'civil_status_de', 'name_and_nationality', 'name_and_swiss',
    'name_and_gender', 'name_and_male', 'name_and_female', 'name_only_en', 'ages_en',
    'civil_status_en', 'name_and_nationality_en', 'name_and_swiss_en',
    'name_and_gender_en', 'name_and_male_en', 'name_and_female_en'
]

models = [
    'gpt-4o-mini', 'claude-3-5-haiku-20241022',
    'gemini-2.0-flash-lite', 'deepseek-chat', 'meta-llama/Llama-3.3-70B-Instruct'
]

credit_types = [
    'Privatkredit', 'Hypothekarkredit', 'Leasing', 'Autokredit',
    'Personal Loan', 'Mortgage Loan', 'Leasing EN', 'Car Loan'
]

output_csv = '../data/output/top1_input_match_distribution.csv'

# Data container
records = []

# Main loop
for feature in tqdm(features, desc="Processing features"):
    for model in models:
        files = glob.glob(f'../data/intermediary/application_ranking/{model}/**/{feature}/**/official_run/*.json', recursive=True)

        # Nested dict: (demo, credit_type) -> input top demo counts
        stats = defaultdict(lambda: {"top_llm": 0, "input_demos": Counter()})

        for fn in files:
            try:
                with open(fn, 'r') as f:
                    data = json.load(f)
            except:
                continue

            context = data.get("context", {})
            credit_type = context.get("credit_type", None)
            if credit_type not in credit_types:
                continue

            real_order = [name.lower() for name in context['default_order']]
            demo_order = context['demo_order']
            name_to_demo = dict(zip(real_order, demo_order))

            # Model output
            sentence = data['choices'][0]['message']['content'].lower()
            name_pos = {name: sentence.find(name) for name in real_order}
            sorted_names = sorted(name_pos.items(), key=lambda x: x[1])
            llm_order = [name for name, pos in sorted_names if pos != -1]

            if not llm_order:
                continue

            llm_top_demo = name_to_demo.get(llm_order[0])
            input_top_demo = demo_order[0]

            if llm_top_demo is None or input_top_demo is None:
                continue

            key = (llm_top_demo, credit_type, model, feature)
            stats[key]["top_llm"] += 1
            stats[key]["input_demos"][input_top_demo] += 1

        # Convert to records
        for (demo, credit_type, model, feature), info in stats.items():
            row = {
                "demo": demo,
                "credit_type": credit_type,
                "model": model,
                "feature": feature,
                "top_llm": info["top_llm"]
            }
            # One column per input demo
            for input_demo, count in info["input_demos"].items():
                row[input_demo] = count
            records.append(row)

# Final DataFrame
df = pd.DataFrame(records)
df.fillna(0, inplace=True)
df = df.astype({col: 'int' for col in df.columns if col not in ['demo', 'credit_type', 'model', 'feature']})
df.to_csv(output_csv, index=False)
print(f"Saved CSV to {output_csv}")

Processing features:   0%|          | 0/16 [00:00<?, ?it/s]

Processing features: 100%|██████████| 16/16 [47:08<00:00, 176.77s/it]


Saved CSV to ../data/output/top1_input_match_distribution.csv


In [ ]:
df = pd.DataFrame(records)
df.fillna(0, inplace=True)
df = df.astype({col: 'int' for col in df.columns if col not in ['demo', 'credit_type', 'model', 'feature']})
df.to_csv(output_csv, index=False)
print(f"Saved CSV to {output_csv}")

Saved CSV to ../data/output/top1_input_match_distribution.csv


In [ ]:
import pandas as pd

# Input/output files
input_csv = '../data/output/top1_input_match_distribution.csv'
output_excel = '../data/output/top1_input_match_distribution_by_feature.xlsx'

# Load the CSV
df = pd.read_csv(input_csv)


with pd.ExcelWriter(output_excel, engine='xlsxwriter') as writer:
    for feature_name, feature_df in df.groupby('feature'):
        
        sheet_name = feature_name[:31]
        feature_df.to_excel(writer, sheet_name=sheet_name, index=False)

print(f"Excel file saved to {output_excel}")

Excel file saved to ../data/output/top1_input_match_distribution_by_feature.xlsx
